In [ ]:
## Code for lecture 5: Computations in TT format
import numpy as np
import matplotlib.pyplot as plt

# We use the scikit_tt toolbox from https://github.com/PGelss/scikit_tt/
# Alternatives include original TT-Toolbox for Matlab

import scikit_tt.tensor_train as tt

# Construct random tt tensors
X1 = tt.TT(np.random.randn(2,3,4,5,6,1,1,1,1,1))
X2 = tt.rand([2,3,4,5,6],[1,1,1,1,1])

# TT-tensors of same size can be added, note that ranks will also add
Y = X1 + X2
print("X1 = ",X1)
print("X2 = ",X2)
print("X1+X2 = ",Y)

# Computer inner product
print("inner product (X1,X2) =",X1.transpose()@X2)


In [ ]:
# We can consider tensors of very high order
d = 25
ndims = np.int_(2*np.ones(d)) # 2^d tensor
r = 5
ranks = np.append([1],np.append(np.int_(r*np.ones(d-1)),[1])) # we always consider first and last rank = 1
X = tt.rand(ndims,np.int_(np.ones(d)),list(ranks)) # encodes tensor with 2^d elements and TT ranks 5

# Construct now a random TT operator (MPO) from 2^d -> 3^d with MPO ranks 4,...,4
ndims2 = np.int_(3*np.ones(d))
s = 4
ranksA = np.append([1],np.append(np.int_(s*np.ones(d-1)),[1]))
A = tt.rand(ndims2,ndims,list(ranksA))

# The MPO A can be multiplied with the 2^d TT-tensor X, resulting in a 3^d tensor
Z = A@X # this corresponds to a mat-vec with a 3^d x 2^d matrix !
print("ranks(A) : ",A.ranks)
print("ranks(X) : ",X.ranks)
print("ranks(AX): ",Z.ranks)

# Note that ranks have been multiplied, but truncation can be applied
Zold = Z.copy()
Z.ortho_left(max_rank=3) # left orthogonalization with rank truncation
print(Z)
print((Z-Zold).norm()/Zold.norm())


In [ ]:
## In this part, TT tensors are used to solve a simplified ML task.
## We follow Exercise 3.1 in the folder 'Exercises' of the scikit_tt repository
import scikit_tt.data_driven.transform as tdt
import scikit_tt.data_driven.regression as reg

# The following file (from the repository) contains a reduced MNIST data set of 500 training and 100 test
# images of size 7x7 representing handwritten digits 1 or 0 (one-hot encoding)
data = np.load('MNIST_reduced.npz')
x_train = data['x_train']
x_test = data['x_test']
y_train = data['y_train']
y_test = data['y_test']

# Example: show images and labels of first two training and last two test samples
fig, (ax1, ax2, ax3, ax4) = plt.subplots(1, 4, figsize=(9, 2))
ax1.imshow(np.reshape(x_train[:,0],[7,7]))
ax2.imshow(np.reshape(x_train[:,1],[7,7]))
ax3.imshow(np.reshape(x_test[:,-2],[7,7]))
ax4.imshow(np.reshape(x_test[:,-1],[7,7]))
plt.show()
print(y_train[:,0],y_train[:,1],y_test[:,-2],y_test[:,-1])

# The feature map is defined to transform data points in R^d into 2x..x2 rank-one tensors
# [cos(a x1), sin(a x2)] \otimes ... \otimes [cos (a xd), sin(a xd)]. Here d = 49 (7x7 images).
d = 49
a = .5*np.pi
basis_list = []
for i in range(d):
   basis_list.append([tdt.Cos(i, a), tdt.Sin(i, a)])

# Solve the kernel regression optimization problem
# random intial guess
cores = [np.ones([1, 2, 1, 1]) for i in range(d)]
initial_guess = tt.TT(cores).ortho()
# Apply dedicated optimization method (alternating ridge regression) from the toolbox for training
xi = reg.arr(x_train, y_train, basis_list, initial_guess, repeats=5, progress=False)

# Evaluate labels of test data using the trained classifier
Theta = tdt.basis_decomposition(x_test, basis_list).transpose(cores=49) # Applies feature map
xi_0 = tt.TT(xi[0].cores + [np.ones([1,1,1,1])])
y_0 = (xi_0.transpose()@Theta).matricize()
xi_1 = tt.TT(xi[1].cores + [np.ones([1,1,1,1])])
y_1 = (xi_1.transpose()@Theta).matricize()
y = np.vstack([y_0,y_1])

# Prediction 0 or 1 is based on the larger entry
labels = np.argmax(y,axis=0)
# Correct values
labels_true = np.argmax(y_test,axis=0)

# Compare with true values y_test
print("Number of test samples:", y.shape[1])
print("Wrong classifications :", np.count_nonzero(labels - labels_true))
